In [1]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [2]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [3]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [4]:
df_net_income_sii = generate_df_for_stocktype(107, 1, 3, 'sii', 'NetIncome', '稅後純益率(%)(稅後純益)/(營業收入)', '營益分析彙總表')

df_net_income_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 1


公司代號     公司名稱 NetIncome(%)_107Q1 NetIncome(%)_106Q4 NetIncome(%)_106Q3  \
0    1101       台泥              11.85              10.50              10.04   
1    1102       亞泥              14.57              10.27               9.55   
2    1103       嘉泥              33.99              46.64              -0.73   
3    1104     環球水泥               0.20              31.54              30.60   
4    1108     幸福水泥              -0.74              -3.00               0.80   
5    1109     信大水泥              16.05              13.21              10.15   
6    1110       東泥               3.72               3.40               0.47   
7    1201     味全公司               3.27               5.03               1.35   
8    1203     味王公司              10.51              12.05              12.47   
9    1210     大成長城               5.40               3.49               3.15   
10   1213       大飲               1.13               0.31               2.18   
11   1215     卜蜂企業               5.44               7.44               7.30   
12   1216       統一               6.26              15.00               7.36   
13   1217      愛之味               3.90               3.50               0.33   
14   1218     泰山企業               4.40               4.13               5.14   
15   1219     福壽實業               1.56               0.51              -0.23   
16   1220       台榮               5.89               3.56               4.18   
17   1225      福懋油               3.44               2.98               3.77   
18   1227       佳格              10.03               8.35               7.88   
19   1229     聯華實業              44.53              61.07              63.58   
20   1231     聯華食品               6.68               5.79               5.17   
21   1232      大統益               4.91               4.93               4.86   
22   1233       天仁               6.97               8.23               8.44   
23   1234       黑松               5.13               5.98               6.43   
24   1235       興泰             150.04             399.16             473.98   
25   1236     宏亞食品               5.88               0.27              -2.03   
26   1256  鮮活果汁-KY               9.32               9.84              10.79   
27   1262    綠悅-KY              -1.83              12.16              15.59   
28   1301       台塑              21.94              23.89              23.77   
29   1303     南亞塑膠              16.14              17.63              16.08   
30   1304       台聚               5.56               4.66               4.75   
31   1305       華夏              14.08               9.11               8.71   
32   1307     三芳化工               4.33               9.14              10.35   
33   1308       亞聚               6.24               8.83               9.87   
34   1309     台達化工               3.92               2.53               1.80   
35   1310       台苯               9.66               6.67               8.06   
36   1312     國喬石化              15.74              14.76              13.58   
37   1313       聯成               3.18               4.63               5.04   
38   1314      中石化              11.62              18.26              20.24   
39   1315     達新工業              -1.54               6.34               9.29   
40   1316       上曜              18.01              15.10              -5.90   
41   1319       東陽               8.06               9.80               9.61   
42   1321       大洋               3.34              -1.82              -0.60   
43   1323       永裕               8.67               9.68               9.58   
44   1324     地球工業              -2.06               4.91               6.70   
45   1325       恒大               3.34               4.59               3.82   
46   1326       台化              14.48              16.75              16.41   
47   1337    再生-KY             -39.92               3.97               5.39   
48   1338    廣華-KY               9.21               9.31               9.33   
49   1339       昭輝               7.24               9.3

In [5]:
df_net_income_otc = generate_df_for_stocktype(107, 1, 3, 'otc', 'NetIncome', '稅後純益率(%)(稅後純益)/(營業收入)', '營益分析彙總表')

df_net_income_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 106
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 105
season: 1
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 4
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 3
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 2
稅後純益率(%)(稅後純益)/(營業收入)
year: 104
season: 1


公司代號    公司名稱 NetIncome(%)_107Q1 NetIncome(%)_106Q4 NetIncome(%)_106Q3  \
0    1258   其祥-KY               1.74               2.45               3.75   
1    1259      安心               1.75               3.02               3.54   
2    1264      德麥              12.02              13.99              14.10   
3    1333     恩得利             -66.59             -29.03             -28.60   
4    1336      台翰               1.89               4.42               4.49   
5    1565    精華光學              22.29              24.76              25.00   
6    1566      捷邦               1.08               2.07               1.76   
7    1569      濱川               0.54               7.74               8.24   
8    1570    力肯實業               7.32               9.47              10.32   
9    1580    新麥企業               5.86              11.86              11.88   
10   1584    精剛精密             -17.46              -8.36              -6.19   
11   1586    和勤精機               2.51               1.36               1.11   
12   1591   駿吉-KY               0.18               0.45               0.99   
13   1593      祺驊               6.12              13.70              12.93   
14   1595    川寶科技               3.77              21.67              10.49   
15   1597      直得              19.68              15.98              14.72   
16   1599     宏佳騰              -3.16               6.07               4.90   
17   1742      台蠟             -16.61               2.10               1.48   
18   1752      南光               9.97              12.36              12.60   
19   1777      生泰              13.57               8.60               8.32   
20   1781    合世生醫             -19.04             -12.73             -12.30   
21   1784    訊聯生技               9.35               0.24               0.10   
22   1785     光洋科               2.64               0.74               0.60   
23   1787     福盈科               5.36               7.45               7.52   
24   1788    杏昌生技               7.70               8.52               8.02   
25   1795    美時製藥               1.68               0.76               1.15   
26   1799      易威             -66.85             -87.46             -80.57   
27   1813     寶利徠               2.66              -4.95              -0.31   
28   1815    富喬工業              12.19              10.11              12.96   
29   2035    唐榮公司              -3.91               1.29               1.88   
30   2061      風青               2.43               2.42               2.22   
31   2063      世鎧              15.14              12.51              13.18   
32   2064      晉椿               0.18               1.00               0.96   
33   2066      世德               3.08              12.76              12.96   
34   2067      嘉鋼               1.55              -3.70              -5.46   
35   2221    大甲永和              11.72               9.66               9.15   
36   2230      泰茂              -7.42              -3.05              -4.24   
37   2233      宇隆              10.79              16.58              16.29   
38   2235      謚源              10.75              13.66              15.67   
39   2596    綠意開發              38.10              28.57              24.61   
40   2640     大車隊              14.00              13.11              13.68   
41   2641    正德海運              16.10             -66.44              -0.53   
42   2718      晶悅              -1.06               1.01              -0.69   
43   2719     燦星旅              -8.30              -4.89              -4.97   
44   2724   富驛-KY             -31.29             -32.44             -26.09   
45   2726   雅茗-KY               6.46               7.67               8.52   
46   2729    瓦城泰統               8.58               7.99               8.66   
47   2732    六角國際               2.49               7.42               7.45   
48   2734     易飛網               0.60              -6.48              -1.61   
49   2736      高野              -2.12              -1.64              -0.36   
50   2740      天蔥          

In [6]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_net_income = pd.concat([df_net_income_sii,df_net_income_otc],axis=0, ignore_index=True)

df_net_income

公司代號     公司名稱 NetIncome(%)_107Q1 NetIncome(%)_106Q4 NetIncome(%)_106Q3  \
0     1101       台泥              11.85              10.50              10.04   
1     1102       亞泥              14.57              10.27               9.55   
2     1103       嘉泥              33.99              46.64              -0.73   
3     1104     環球水泥               0.20              31.54              30.60   
4     1108     幸福水泥              -0.74              -3.00               0.80   
5     1109     信大水泥              16.05              13.21              10.15   
6     1110       東泥               3.72               3.40               0.47   
7     1201     味全公司               3.27               5.03               1.35   
8     1203     味王公司              10.51              12.05              12.47   
9     1210     大成長城               5.40               3.49               3.15   
10    1213       大飲               1.13               0.31               2.18   
11    1215     卜蜂企業               5.44               7.44               7.30   
12    1216       統一               6.26              15.00               7.36   
13    1217      愛之味               3.90               3.50               0.33   
14    1218     泰山企業               4.40               4.13               5.14   
15    1219     福壽實業               1.56               0.51              -0.23   
16    1220       台榮               5.89               3.56               4.18   
17    1225      福懋油               3.44               2.98               3.77   
18    1227       佳格              10.03               8.35               7.88   
19    1229     聯華實業              44.53              61.07              63.58   
20    1231     聯華食品               6.68               5.79               5.17   
21    1232      大統益               4.91               4.93               4.86   
22    1233       天仁               6.97               8.23               8.44   
23    1234       黑松               5.13               5.98               6.43   
24    1235       興泰             150.04             399.16             473.98   
25    1236     宏亞食品               5.88               0.27              -2.03   
26    1256  鮮活果汁-KY               9.32               9.84              10.79   
27    1262    綠悅-KY              -1.83              12.16              15.59   
28    1301       台塑              21.94              23.89              23.77   
29    1303     南亞塑膠              16.14              17.63              16.08   
30    1304       台聚               5.56               4.66               4.75   
31    1305       華夏              14.08               9.11               8.71   
32    1307     三芳化工               4.33               9.14              10.35   
33    1308       亞聚               6.24               8.83               9.87   
34    1309     台達化工               3.92               2.53               1.80   
35    1310       台苯               9.66               6.67               8.06   
36    1312     國喬石化              15.74              14.76              13.58   
37    1313       聯成               3.18               4.63               5.04   
38    1314      中石化              11.62              18.26              20.24   
39    1315     達新工業              -1.54               6.34               9.29   
40    1316       上曜              18.01              15.10              -5.90   
41    1319       東陽               8.06               9.80               9.61   
42    1321       大洋               3.34              -1.82              -0.60   
43    1323       永裕               8.67               9.68               9.58   
44    1324     地球工業              -2.06               4.91               6.70   
45    1325       恒大               3.34               4.59               3.82   
46    1326       台化              14.48              16.75              16.41   
47    1337    再生-KY             -39.92               3.97               5.39   
48    1338    廣華-KY               9.21               9.31               9.33   
49    

In [7]:
#檢查column資料型態

#df_net_income.info() #non-null object
#df_net_income.dtypes #object
#df_net_income.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
NetIncome(%)_107Q1    float64
NetIncome(%)_106Q4    float64
NetIncome(%)_106Q3    float64
NetIncome(%)_106Q2    float64
NetIncome(%)_106Q1    float64
NetIncome(%)_105Q4    float64
NetIncome(%)_105Q3    float64
NetIncome(%)_105Q2    float64
NetIncome(%)_105Q1    float64
NetIncome(%)_104Q4    float64
NetIncome(%)_104Q3    float64
NetIncome(%)_104Q2    float64
NetIncome(%)_104Q1    float64
dtype: object
'''

df_net_income = df_net_income.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_net_income.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號                    int64
公司名稱                   object
NetIncome(%)_107Q1    float64
NetIncome(%)_106Q4    float64
NetIncome(%)_106Q3    float64
NetIncome(%)_106Q2    float64
NetIncome(%)_106Q1    float64
NetIncome(%)_105Q4    float64
NetIncome(%)_105Q3    float64
NetIncome(%)_105Q2    float64
NetIncome(%)_105Q1    float64
NetIncome(%)_104Q4    float64
NetIncome(%)_104Q3    float64
NetIncome(%)_104Q2    float64
NetIncome(%)_104Q1    float64
dtype: object

In [8]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [9]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['NetIncome(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['NetIncome(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['NetIncome(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [10]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['NetIncome(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [11]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_net_income['Growth_{0}Q{1}'.format(year, season)] = df_net_income.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [12]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_net_income['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_net_income.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [13]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [14]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [15]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_net_income = df_net_income.merge(df_basicinfo, on='公司代號', how='inner')

df_net_income

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  NetIncome(%)_107Q1  NetIncome(%)_106Q4  \
0     1101       台泥               11.85               10.50   
1     1102       亞泥               14.57               10.27   
2     1103       嘉泥               33.99               46.64   
3     1104     環球水泥                0.20               31.54   
4     1108     幸福水泥               -0.74               -3.00   
5     1109     信大水泥               16.05               13.21   
6     1110       東泥                3.72                3.40   
7     1201     味全公司                3.27                5.03   
8     1203     味王公司               10.51               12.05   
9     1210     大成長城                5.40                3.49   
10    1213       大飲                1.13                0.31   
11    1215     卜蜂企業                5.44                7.44   
12    1216       統一                6.26               15.00   
13    1217      愛之味                3.90                3.50   
14    1218     泰山企業                4.40                4.13   
15    1219     福壽實業                1.56                0.51   
16    1220       台榮                5.89                3.56   
17    1225      福懋油                3.44                2.98   
18    1227       佳格               10.03                8.35   
19    1229     聯華實業               44.53               61.07   
20    1231     聯華食品                6.68                5.79   
21    1232      大統益                4.91                4.93   
22    1233       天仁                6.97                8.23   
23    1234       黑松                5.13                5.98   
24    1235       興泰              150.04              399.16   
25    1236     宏亞食品                5.88                0.27   
26    1256  鮮活果汁-KY                9.32                9.84   
27    1262    綠悅-KY               -1.83               12.16   
28    1301       台塑               21.94               23.89   
29    1303     南亞塑膠               16.14               17.63   
30    1304       台聚                5.56                4.66   
31    1305       華夏               14.08                9.11   
32    1307     三芳化工                4.33                9.14   
33    1308       亞聚                6.24                8.83   
34    1309     台達化工                3.92                2.53   
35    1310       台苯                9.66                6.67   
36    1312     國喬石化               15.74               14.76   
37    1313       聯成                3.18                4.63   
38    1314      中石化               11.62               18.26   
39    1315     達新工業               -1.54                6.34   
40    1316       上曜               18.01               15.10   
41    1319       東陽                8.06                9.80   
42    1321       大洋                3.34               -1.82   
43    1323       永裕                8.67                9.68   
44    1324     地球工業               -2.06                4.91   
45    1325       恒大                3.34                4.59   
46    1326       台化               14.48               16.75   
47    1337    再生-KY              -39.92                3.97   
48    1338    廣華-KY                9.21                9.31   
49    1339       昭輝                7.24                9.30   
50    1340    勝悅-KY               14.98               24.52   
51    1402      遠東新                7.97                6.52   
52    1410       南染               15.89               19.13   
53    1413     宏洲纖維                5.70                3.71   
54    1414       東和                2.09               11.30   
55    1416       廣豐              143.84                9.92   
56    1417       嘉裕              -13.50              -22.58   
57    1418       東華              -38.89              -19.64   
58    1419       新紡              -16.74               82.83   
59    1423     利華羊毛                7.72                6.74   
60    1432    大魯閣實業              -31.12              -15.31   
61    1434     福懋興業                3.56               11.69   
62    1435     中福國際              -48.

In [16]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_net_income.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_NetIncome.xlsx', 'NetIncome_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3', 'Growth_105Q2', '2QMAGrowth_105Q2']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
